In [ ]:
import pandas as pd
import numpy as np
import requests
import time
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
from pandas import datetime
import datedelta
import plotly
plotly.tools.set_credentials_file(username='sasi_ynwa', api_key='wEm5TtVT8TOVKzFyd8CA')
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

In [ ]:
r = requests.get(url='https://poloniex.com/public?command=returnChartData&currencyPair=USDT_ETH&end=9999999999&period=14400&start=1405699200')

In [ ]:
dfETH = pd.DataFrame.from_records(r.json())

In [ ]:
start =time.time()#works but first create a column wiht DateTime
dfETH['DateTime'] = pd.Series(np.random.randn(len(dfETH)), index=dfETH.index)
for i, row in dfETH.iterrows():
    dfETH['DateTime'][i] = datetime.fromtimestamp(row['date']).strftime("%m-%d-%Y %H:%M:%S")
dfETH['DateTime'] =  pd.to_datetime(dfETH['DateTime'], format='%m-%d-%Y %H:%M:%S')
end = time.time()
print(end - start)

C:\Users\msasi\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\Users\msasi\Anaconda3\lib\site-packages\pandas\core\indexing.py:179: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [5]:
dfETH.head()

close        date  high  low  open  quoteVolume      volume  \
0   1.85  1439006400  1.85  0.5  1.65    84.016385  144.428193   
1   1.40  1439020800  1.70  1.4  1.70    92.523053  129.575776   
2   1.40  1439035200  1.40  1.4  1.40     0.000000    0.000000   
3   1.40  1439049600  1.40  1.4  1.40     0.000000    0.000000   
4   1.40  1439064000  1.40  1.4  1.40     0.000000    0.000000   

   weightedAverage            DateTime  
0         1.719048 2015-08-07 23:00:00  
1         1.400470 2015-08-08 03:00:00  
2         1.400000 2015-08-08 07:00:00  
3         1.400000 2015-08-08 11:00:00  
4         1.400000 2015-08-08 15:00:00

In [33]:
#Using Roller to generate Moving Averages(Simple). Here we re multiplying by 6 cos each day has 6 recordings
#roller = dfETH['close'].rolling(10*6)
dfETH['5DayMA'] = dfETH['close'].ewm(span=30, adjust=False).mean()

dfETH['10DayMA'] = dfETH['close'].ewm(span=60, adjust=False).mean()

#roller = dfETH['close'].rolling(30*6)
dfETH['30DayMA'] = dfETH['close'].ewm(span=180, adjust=False).mean()

#roller = dfETH['close'].rolling(50*6)
#dfETH['50DayMA'] = roller.mean()
dfETH['50DayMA'] = dfETH['close'].ewm(span=300, adjust=False).mean()

In [34]:
data = [
    go.Scatter(
        x=dfETH['DateTime'], # assign x as the dataframe column 'x'
        y=dfETH['close'],
        name = 'Closing Price'
    ),
    go.Scatter(
        x = dfETH['DateTime'],
        y = dfETH['5DayMA'],
        name = '5DayMA'
    ),
    go.Scatter(
        x = dfETH['DateTime'],
        y = dfETH['30DayMA'],
        name = '30DayMA'
    ),
    go.Scatter(
        x = dfETH['DateTime'],
        y = dfETH['10DayMA'],
        name = '10DayMA'
    ),
    #go.Scatter(
     #   x = dfETH['DateTime'],
      #  y = dfETH['weightedAverage'],
       # name = 'Weighted Average Price'
    #)#,
    #go.Candlestick(x=dfETH.DateTime,
     #                  open=dfETH.open,
      #                 high=dfETH.high,
       #                low=dfETH.low,
        #               close=dfETH.close,
         #              increasing=dict(line=dict(color= '#17BECF')),
          #             decreasing=dict(line=dict(color= '#7F7F7F')))
]
# IPython notebook
plotly.offline.iplot(data)

If the Orange line which is the 50 Day MA is at the bottom the price is going to go up. But if the 50 Day MA is at the top and the other two MA are at the bottom then the price is going to fall down. Once the 10 Day MA moves below 30 Day MA and 50 Day MA we can see that the price will continuw to fall till the 50 Day MA can bring them up.

In [13]:
#Using Roller to generate Moving Averages(Simple) for Volume
#roller = dfETH['volume'].rolling(10*6)
dfETH['Vol10DayMA'] = dfETH['volume'].ewm(span=60, adjust=False).mean()

#roller = dfETH['volume'].rolling(30*6)
dfETH['Vol30DayMA'] = dfETH['volume'].ewm(span=180, adjust=False).mean()

#roller = dfETH['volume'].rolling(50*6)
dfETH['Vol50DayMA'] = dfETH['volume'].ewm(span=300, adjust=False).mean()

In [14]:
data = [
    go.Scatter(
        x=dfETH['DateTime'], # assign x as the dataframe column 'x'
        y=dfETH['volume'],
        name = 'Volume'
    ),
    go.Scatter(
        x = dfETH['DateTime'],
        y = dfETH['Vol50DayMA'],
        name = '50DayMA - Volume'
    ),
    go.Scatter(
        x = dfETH['DateTime'],
        y = dfETH['Vol30DayMA'],
        name = '30DayMA - Volume'
    ),
    go.Scatter(
        x = dfETH['DateTime'],
        y = dfETH['Vol10DayMA'],
        name = '10DayMA - Volume'
    )#,
    #go.Candlestick(x=dfETH.DateTime,
     #                  open=dfETH.open,
      #                 high=dfETH.high,
       #                low=dfETH.low,
        #               close=dfETH.close,
         #              increasing=dict(line=dict(color= '#17BECF')),
          #             decreasing=dict(line=dict(color= '#7F7F7F')))
]
# IPython notebook
plotly.offline.iplot(data)

In [43]:
dfETH['Volatility'] = pd.Series(np.random.randn(len(dfETH)), index=dfETH.index)

In [54]:
#New try, Volatility window is for 3 days shift should be done -1 since we are comparing results with 1 up 
#here we have taken log of returns and hence there is no -1 at the end(this was done when referred to investopedia.com)

dfETH['Log_Returns'] = np.log(dfETH['close'] / dfETH['close'].shift(-1))# - 1)

#The below line would remember the three day event but will forget soon afterwards.
#dfETH['Volatility_const_wind'] = pd.rolling_std(dfETH['Log_Returns'], window=18)

#here we have a decaying effect for 3 days in the below line
dfETH['Volatility'] = dfETH['Log_Returns'].ewm(span=18, adjust=False).std()

In [55]:
#Using Roller to generate Moving Averages(Simple) for Volatility
#roller = dfETH['Volatility'].rolling(10*6)
dfETH['Volatility10DayMA'] = dfETH['Volatility'].ewm(span=60, adjust=False).mean()
#dfETH['Volatility10DayMA_const'] = dfETH['Volatility_const_wind'].ewm(span=60, adjust=False).mean()
#roller = dfETH['Volatility'].rolling(30*6)
dfETH['Volatility30DayMA'] = dfETH['Volatility'].ewm(span=180, adjust=False).mean()

#roller = dfETH['Volatility'].rolling(50*6)
dfETH['Volatility50DayMA'] = dfETH['Volatility'].ewm(span=300, adjust=False).mean()

In [56]:
dfETH['meanLineVolatility'] = dfETH['Volatility'].mean()

data = [
    go.Scatter(
        x=dfETH['DateTime'], # assign x as the dataframe column 'x'
        y=dfETH['Volatility'],
        name = 'Volatility'
    ),
    go.Scatter(
        x=dfETH['DateTime'], # assign x as the dataframe column 'x'
        y=dfETH['meanLineVolatility'],
        name = 'Volatility mean Line'
    ),
    go.Scatter(
        x = dfETH['DateTime'],
        y = dfETH['Volatility10DayMA'],
        name = '10DayMA - Volatility'
    )#,
    #go.Scatter(
     #   x = dfETH['DateTime'],
      #  y = dfETH['Volatility30DayMA'],
       # name = '30DayMA - Volatility'
    #)#,
   # go.Scatter(
    #    x = dfETH['DateTime'],
     #   y = dfETH['Volatility50DayMA'],
      #  name = '50DayMA - Volatility'
    #)#,
    #go.Candlestick(x=dfETH.DateTime,
     #                  open=dfETH.open,
      #                 high=dfETH.high,
       #                low=dfETH.low,
        #               close=dfETH.close,
         #              increasing=dict(line=dict(color= '#17BECF')),
          #             decreasing=dict(line=dict(color= '#7F7F7F')))
]
# IPython notebook
plotly.offline.iplot(data)

Volatility is still pretty high meaning the price is spread out over a large range of values. This means that the price of the ETH can change dramatically over a short time period in either direction. A lower volatility means that a security's value does not fluctuate dramatically, but changes in value at a steady pace over a period of time.


In [25]:
sharpe_ratio = (dfETH['Returns'].mean() - 2.83) / dfETH['Volatility30DayMA'].mean()

In [26]:
sharpe_ratio

-82.4702421290584

In [28]:
dfETH['Returns'].describe()

count    5753.000000
mean       -0.000176
std         0.041617
min        -0.367232
25%        -0.011838
50%         0.000000
75%         0.009985
max         1.121212
Name: Returns, dtype: float64

In [29]:
dfETH['Volatility30DayMA'].mean()

0.034317546370369705

In [30]:
dfETH.head()

close        date  high  low  open  quoteVolume      volume  \
0   1.85  1439006400  1.85  0.5  1.65    84.016385  144.428193   
1   1.40  1439020800  1.70  1.4  1.70    92.523053  129.575776   
2   1.40  1439035200  1.40  1.4  1.40     0.000000    0.000000   
3   1.40  1439049600  1.40  1.4  1.40     0.000000    0.000000   
4   1.40  1439064000  1.40  1.4  1.40     0.000000    0.000000   

   weightedAverage            DateTime   10DayMA         ...          \
0         1.719048 2015-08-07 23:00:00  1.850000         ...           
1         1.400470 2015-08-08 03:00:00  1.835246         ...           
2         1.400000 2015-08-08 07:00:00  1.820976         ...           
3         1.400000 2015-08-08 11:00:00  1.807173         ...           
4         1.400000 2015-08-08 15:00:00  1.793823         ...           

     5DayMA  Vol10DayMA  Vol30DayMA  Vol50DayMA   Returns  Volatility  \
0  1.850000  144.428193  144.428193  144.428193  0.321429         NaN   
1  1.820968  143.941228  144.264077  144.329505  0.000000         NaN   
2  1.793809  139.221844  142.669999  143.370505  0.000000         NaN   
3  1.768402  134.657193  141.093535  142.417877  0.000000         NaN   
4  1.744634  130.242203  139.534491  141.471579  0.000000         NaN   

   Volatility10DayMA  Volatility30DayMA  Volatility50DayMA  meanLineVolatility  
0                NaN                NaN                NaN            0.030519  
1                NaN                NaN                NaN            0.030519  
2                NaN                NaN                NaN            0.030519  
3                NaN                NaN                NaN            0.030519  
4                NaN                NaN                NaN            0.030519  

[5 rows x 22 columns]